In [48]:
! git clone https://github.com/uf-hobi-informatics-lab/ClinicalTransformerNER.git

Cloning into 'ClinicalTransformerNER'...
remote: Enumerating objects: 92, done.
remote: Counting objects: 100% (92/92), done.
remote: Compressing objects: 100% (62/62), done.
remote: Total 92 (delta 37), reused 73 (delta 25), pack-reused 0
Unpacking objects: 100% (92/92), done.


In [1]:
import sys
sys.path.append("./ClinicalTransformerNER/")
sys.path.append("./NLPpreprocessing-master/")
import os
from pathlib import Path
from collections import defaultdict, Counter
import numpy as np
from sklearn.model_selection import train_test_split
import shutil 
from annotation2BIO import generate_BIO, pre_processing, read_annotation_brat, BIOdata_to_file
MIMICIII_PATTERN = "\[\*\*|\*\*\]"

In [2]:
! ls


bio			new_round_merged_1_2
ClinicalTransformerNER	NLPpreprocessing-master
data			round_3_output
log.txt			round_3_output_formatted_output
new_round_3		round_4_output_formatted_output
new_round_4		SDOH_bert
new_round_merged	SDoH_ner.ipynb


In [3]:
! pwd

/home/zehao.yu/workspace/py3/SDoH


In [62]:
all_root='./new_round_merged/'

In [42]:
training_root='./new_round_merged_1_2/'

In [63]:
# Brief descriptive statistics
file_ids = set()
enss = []

for fn in Path(all_root).glob("*.ann"):
    file_ids.add(fn.stem)
    _, ens, _ = read_annotation_brat(fn)
    #print( _)
    enss.extend(ens)
print("training files: ", len(file_ids), list(file_ids)[:5])
print("total training eneitites: ", len(enss))
print("Entities distribution by types:\n", "\n".join([str(c) for c in Counter([each[1] for each in enss]).most_common()]))

training files:  120 ['IRB201901754_NOTE_641085_1', 'IRB201901754_NOTE_538086_8', 'IRB201901754_NOTE_1180173_0', 'IRB201901754_NOTE_1184717_0', 'IRB201901754_NOTE_1232797_0']
total training eneitites:  3024
Entities distribution by types:
 ('Substance_use_status', 461)
('Sdoh_status', 438)
('Gender', 167)
('Smoking_type', 146)
('Social_cohesion', 142)
('Abuse', 130)
('Education', 119)
('Alcohol_use', 111)
('Marital_status', 103)
('Occupation', 97)
('Smoking_freq_ppd', 97)
('Drug_use', 96)
('Tobacco_use', 86)
('Sex_act', 83)
('Living_supply', 83)
('Physical_act', 70)
('Smoking_freq_sy', 64)
('Sdoh_freq', 61)
('Transportation', 55)
('Smoking_freq_qy', 52)
('Alcohol_freq', 46)
('Partner', 38)
('Race', 31)
('Financial_constrain', 29)
('Living_Condition', 27)
('Smoking_freq_py', 26)
('Drug_type', 23)
('SDoH_ICD', 20)
('Smoking_freq_other', 19)
('Alcohol_type', 19)
('Employment_status', 19)
('Alcohol_other', 17)
('Protection', 10)
('Ethnicity', 8)
('Employment_location', 7)
('Language', 6)
(

In [51]:
# generate BIO from brat annotation
train_root = Path(training_root)
train_bio = "./bio/trains/"
output_root = Path(train_bio)
output_root.mkdir(parents=True, exist_ok=True)

for fid in file_ids:
    txt_fn = train_root / (fid + ".txt")
    ann_fn = train_root / (fid + ".ann")
    bio_fn = output_root / (fid + ".bio.txt")
    
    txt, sents = pre_processing(txt_fn, deid_pattern=MIMICIII_PATTERN)
    e2idx, entities, rels = read_annotation_brat(ann_fn)
    nsents, sent_bound = generate_BIO(sents, entities, file_id=fid, no_overlap=False)
    #print(nsents)
    BIOdata_to_file(bio_fn, nsents)

2020-10-16 18:08:34,705 INFO sentence boundary detection class initiated.
2020-10-16 18:08:34,706 INFO word level tokenization with replace_number set to False
2020-10-16 18:08:34,706 INFO current processing new_round_merged_1_2/IRB201901754_NOTE_641085_1.txt ...
2020-10-16 18:08:34,714 WARNING '1.73M2' cannot be parsed by current rule.
2020-10-16 18:08:34,715 WARNING '1.73M2' cannot be parsed by current rule.
2020-10-16 18:08:34,741 INFO process IRB201901754_NOTE_641085_1 file
2020-10-16 18:08:34,742 WARNING ('[**DATE**]', 'Smoking_freq_qy', (368, 378)) offset is overlapped with previous entity; current tok not overlap
2020-10-16 18:08:34,812 INFO sentence boundary detection class initiated.
2020-10-16 18:08:34,813 INFO word level tokenization with replace_number set to False
2020-10-16 18:08:34,814 INFO current processing new_round_merged_1_2/IRB201901754_NOTE_538086_8.txt ...
2020-10-16 18:08:34,832 INFO process IRB201901754_NOTE_538086_8 file
2020-10-16 18:08:34,899 INFO sentence b

2020-10-16 18:08:36,528 INFO current processing new_round_merged_1_2/IRB201901754_NOTE_732823_0.txt ...
2020-10-16 18:08:36,562 INFO process IRB201901754_NOTE_732823_0 file
2020-10-16 18:08:36,614 INFO sentence boundary detection class initiated.
2020-10-16 18:08:36,615 INFO word level tokenization with replace_number set to False
2020-10-16 18:08:36,616 INFO current processing new_round_merged_1_2/note_15031_0.txt ...
2020-10-16 18:08:36,662 INFO process note_15031_0 file
2020-10-16 18:08:36,720 INFO sentence boundary detection class initiated.
2020-10-16 18:08:36,720 INFO word level tokenization with replace_number set to False
2020-10-16 18:08:36,721 INFO current processing new_round_merged_1_2/IRB201901754_NOTE_704519_1.txt ...
2020-10-16 18:08:36,747 INFO process IRB201901754_NOTE_704519_1 file
2020-10-16 18:08:36,818 INFO sentence boundary detection class initiated.
2020-10-16 18:08:36,819 INFO word level tokenization with replace_number set to False
2020-10-16 18:08:36,819 INFO 

2020-10-16 18:08:38,631 INFO process IRB201901754_NOTE_352025_2 file
2020-10-16 18:08:38,632 WARNING ('[**DATE**]', 'Smoking_freq_qy', (5065, 5075)) offset is overlapped with previous entity; current tok not overlap
2020-10-16 18:08:38,632 WARNING ('[**DATE**]', 'Smoking_freq_qy', (5124, 5134)) offset is overlapped with previous entity; current tok not overlap
2020-10-16 18:08:38,633 WARNING ('beer', 'Alcohol_type', (5179, 5183)) offset is overlapped with previous entity; current tok not overlap
2020-10-16 18:08:38,633 WARNING ('[**DATE**]', 'Alcohol_other', (5214, 5224)) offset is overlapped with previous entity; current tok not overlap
2020-10-16 18:08:38,699 INFO sentence boundary detection class initiated.
2020-10-16 18:08:38,700 INFO word level tokenization with replace_number set to False
2020-10-16 18:08:38,701 INFO current processing new_round_merged_1_2/note_186896_4.txt ...
2020-10-16 18:08:38,730 INFO process note_186896_4 file
2020-10-16 18:08:38,731 WARNING ('[**DATE**]', 

2020-10-16 18:08:40,263 INFO current processing new_round_merged_1_2/note_120443_1.txt ...
2020-10-16 18:08:40,286 INFO process note_120443_1 file
2020-10-16 18:08:40,336 INFO sentence boundary detection class initiated.
2020-10-16 18:08:40,337 INFO word level tokenization with replace_number set to False
2020-10-16 18:08:40,338 INFO current processing new_round_merged_1_2/note_90924_1.txt ...
2020-10-16 18:08:40,376 INFO process note_90924_1 file
2020-10-16 18:08:40,377 WARNING ('[**DATE**]', 'Smoking_freq_qy', (4620, 4630)) offset is overlapped with previous entity; current tok not overlap
2020-10-16 18:08:40,450 INFO sentence boundary detection class initiated.
2020-10-16 18:08:40,451 INFO word level tokenization with replace_number set to False
2020-10-16 18:08:40,451 INFO current processing new_round_merged_1_2/IRB201901754_NOTE_513313_2.txt ...
2020-10-16 18:08:40,474 INFO process IRB201901754_NOTE_513313_2 file
2020-10-16 18:08:40,525 INFO sentence boundary detection class initi

2020-10-16 18:08:42,076 INFO process IRB201901754_NOTE_760457_0 file
2020-10-16 18:08:42,127 INFO sentence boundary detection class initiated.
2020-10-16 18:08:42,128 INFO word level tokenization with replace_number set to False
2020-10-16 18:08:42,129 INFO current processing new_round_merged_1_2/IRB201901754_NOTE_1097824_0.txt ...
2020-10-16 18:08:42,156 INFO process IRB201901754_NOTE_1097824_0 file
2020-10-16 18:08:42,225 INFO sentence boundary detection class initiated.
2020-10-16 18:08:42,226 INFO word level tokenization with replace_number set to False
2020-10-16 18:08:42,226 INFO current processing new_round_merged_1_2/note_107645_0.txt ...
2020-10-16 18:08:42,243 INFO process note_107645_0 file
2020-10-16 18:08:42,307 INFO sentence boundary detection class initiated.
2020-10-16 18:08:42,308 INFO word level tokenization with replace_number set to False
2020-10-16 18:08:42,308 INFO current processing new_round_merged_1_2/note_286713_0.txt ...
2020-10-16 18:08:42,351 INFO process n

In [41]:
with open('./bio/train.txt') as f:
    for line in f:
        fea=line.split(' ')
        if len(fea)>1:
            for k in fea[1:5]:
                if k == 'o':
                    print(line)
        
            

In [52]:
# train dev split
file_ids = list(file_ids)
train_ids, dev_ids = train_test_split(file_ids, train_size=0.9, random_state=13, shuffle=True)
len(train_ids), len(dev_ids)

(90, 10)

In [53]:
# merge previous bio results into train.txt and dev.txt
import fileinput

# train
with open("./bio/train.txt", "w") as f:
    for fid in train_ids:
        f.writelines(fileinput.input(output_root / (fid + ".bio.txt")))
    fileinput.close()
        
# dev
with open("./bio/dev.txt", "w") as f:
    for fid in dev_ids:
        f.writelines(fileinput.input(output_root / (fid + ".bio.txt")))
    fileinput.close()
    
# now you can check your ./2018n2c2/bio, there should be two new files train.txt and dev.txt
! ls -l ./bio

total 6024
-rw-rw-r--. 1 zehao.yu zehao.yu  523900 Oct 16 18:08 dev.txt
drwxrwxr-x. 2 zehao.yu zehao.yu    8192 Oct 16 15:59 trains
-rw-rw-r--. 1 zehao.yu zehao.yu 5631935 Oct 16 18:08 train.txt


In [ ]:
#train ner
! export CUDA_VISIBLE_DEVICES=0  # indicate no GPU; if you have two GPUs then the IDs for them will be 0 and 1
#MKL_THREADING_LAYER=GNU
! MKL_THREADING_LAYER=GNU python ./ClinicalTransformerNER/src/run_transformer_ner.py \
      --model_type bert \
      --pretrained_model bert-base-uncased \
      --data_dir ./bio \
      --new_model_dir ./SDOH_bert \
      --overwrite_model_dir \
      --max_seq_length 128 \
      --data_has_offset_information \
      --save_model_core \
      --do_train \
      --model_selection_scoring strict-f_score-1 \
      --do_lower_case \
      --train_batch_size 8 \
      --train_steps 1000 \
      --learning_rate 1e-5 \
      --num_train_epochs 20 \
      --gradient_accumulation_steps 1 \
      --do_warmup \
      --seed 13 \
      --warmup_ratio 0.1 \
      --max_num_checkpoints 3 \
      --log_file ./log.txt \
      --progress_bar \
      --early_stop 3 

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertNerModel: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertNerModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPretraining model).
- This IS NOT expected if you are initializing BertNerModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertNerModel were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 

Batch:  34%|███████████                      | 372/1109 [03:29<06:57,  1.76it/s]


Batch:  51%|████████████████▊                | 566/1109 [05:18<05:07,  1.77it/s]


Batch:  69%|██████████████████████▌          | 760/1109 [07:08<03:18,  1.75it/s]


Batch:  86%|████████████████████████████▍    | 954/1109 [08:57<01:27,  1.78it/s]


...

Batch:  80%|██████████████████████████▍      | 888/1109 [12:18<02:58,  1.24it/s]


Batch:  98%|███████████████████████████████▏| 1082/1109 [14:56<00:21,  1.23it/s]


Batch:   2%|▌                                 | 17/1109 [00:13<14:37,  1.24it/s]

evaluation:   0%|                                        | 0/88 [00:00<?, ?it/s]

evaluation:   1%|▎                               | 1/88 [00:00<00:14,  6.20it/s]

evaluation:   2%|▋                               | 2/88 [00:00<00:14,  5.78it/s]

evaluation:   3%|█                               | 3/88 [00:00<00:14,  5.97it/s]

evaluation:   5%|█▍                              | 4/88 [00:00<00:14,  5.63it/s]

evaluation:   6%|█▊                              | 5/88 [00:00<00:14,  5.80it/s]

evaluation:   7%|██▏                             | 6/88 [00:01<00:14,  5.53it/s]

evaluation:   8%|██▌                             | 7/88 [00:01<00:14,  5.75it/s]

evaluation:   9%|██▉                             | 8/88 [00:01<00:14,  5.49it/s]

evaluation:  10%|███▎                            | 9/88 [00:01<00:13,  5.68it/s]

evaluation:  11%|███▌                           | 10/88 [00:01<00:14,  5.48it/s]

evaluation:  12%

Batch:  24%|███████▉                         | 267/1109 [03:58<11:32,  1.22it/s]


Batch:  39%|████████████▉                    | 435/1109 [06:14<09:16,  1.21it/s]

In [56]:
test_root='./new_round_3'

In [55]:
cat ./log.txt

2020-10-16 16:03:26 - Transformer_NER - INFO - Task will use cuda device: GPU_0.
2020-10-16 16:03:26 - Transformer_NER - WARNING - set tokenizer as bert-base-uncased
2020-10-16 16:03:26 - Transformer_NER - WARNING - set config as bert-base-uncased
2020-10-16 16:03:27 - Transformer_NER - WARNING - dev set has label ({'I-PHYSICAL_ACTIVITY', 'B-PHYSICAL_ACTIVITY', 'B-SMOKING', 'B-GENEDER'}) not appeared in train set.
2020-10-16 16:03:27 - Transformer_NER - INFO - Training/evaluation parameters: {'model_type': 'bert', 'pretrained_model': 'bert-base-uncased', 'config_name': 'bert-base-uncased', 'tokenizer_name': 'bert-base-uncased', 'data_dir': './bio', 'data_has_offset_information': True, 'new_model_dir': './SDOH_bert', 'save_model_core': True, 'predict_output_file': None, 'overwrite_model_dir': True, 'seed': 13, 'max_seq_length': 128, 'do_train': True, 'model_selection_scoring': 'strict-f_score-1', 'do_predict': False, 'use_crf': False, 'do_lower_case': True, 'train_batch_size': 8, 'eval_

Gait : ambulates without difficulty Speech : Rate : normal Volume : soft Quality : normal rate , rhythm , and articulation Thought process : coherent and well organized Associations : intact Thought content : denies any psychotic process ( including paranoia , hallucinations or delusions ) , SI or HI Judgement : poor Insight : impaired , based on denial of illness Oriented to person , place , time / date , situation , day of week , month , year Memory : remote and recent memory grossly intact Attention / Concentration : attentive Language : adequate Fund of knowledge : adequate Mood : irritable Affect : smiling inappropriately Minor has developmentally appropriate capacity assent to hospitalization and treatment decisions yes .

2020-10-16 16:03:42 - Transformer_NER - WARNING - 
Sentence after tokenization is too long (expect less than 126 but got 239).
You have to increase max_seq_length to make sure every sentence after tokenization is not longer than the max_seq_length.
Or you can f

You have to increase max_seq_length to make sure every sentence after tokenization is not longer than the max_seq_length.
Or you can further split you long sentences into shorter ones. We will defaultly segment the sentence to two or more seqs with length as (~max_seq_len * n + rest).
The extra long sentence: 
White , 9 th Grade , grades are okay Family : lives with mother and stepfather in LOCATION _ CITY Legal problems : denies Alledged abuse : denies Custody : Bio Mother Home Medications : No prescriptions prior to admission Current Hospital Medications : Scheduled : Continuous Infusions : PRN : acetaminophen 325 mg Oral Q 6 H PRN Or acetaminophen 325 mg Oral Q 6 H PRN aluminum - mag hydroxide - simethicone 30 mL Oral Q 4 H PRN magnesium hydroxide 10 mL Oral Daily PRN No Known Allergies Food allergies : no Environmental allergies : no Review of Systems : Neurological : headache weakness numbness negative but , some mild main in injuries location Cardiovascular : chest pain palpitati

• Snores • SOB ( shortness of breath ) on exertion • Swelling legs PSH : Past Surgical History Procedure Laterality Date • Cervical discectomy 1993 • Cesarean section 1988 • Colonoscopy 2 - 2 - 2012 hyperplastic polyp • Inner ear surgery • Breast biopsy 2012 • Breast lumpectomy 5 - 2012 right breast cancer • Tonsillectomy • Tubal ligation • Biopsy / excision breast Right 10 / 22 / 2014 BIOPSY / EXCISION BREAST performed by Samiian , Laila , MD at JAX MAIN OR • Ultrasonic guidance for needle placement to bx , aspirate , inject , localize w / imaging supervision Right 10 / 22 / 2014 US guided intraoperative needle localizationa performed by Samiian , Laila , MD at JAX MAIN OR • Laparoscopic hysterectomy w / vaginal approach ( lavh ) N / A 6 / 4 / 2015 LAPAROSCOPIC HYSTERECTOMY W / VAGINAL APPROACH ( LAVH ) performed by Jones , James L , MD at JAX MAIN OR • Hysterectomy abdominal 6 / 4 / 2015 HYSTERECTOMY ABDOMINAL performed by Jones , James L , MD at JAX MAIN OR • Eye - anterior chamber 

Social History Main Topics • Smoking status : Former Smoker Quit date : 01 / 01 / 2010 • Smokeless tobacco : Never Used • Alcohol Use : Yes Comment : prior to pregnancy • Drug Use : No • Sexually Active : Not Currently - - Male partner ( s ) Birth Control / Protection : None Other Topics Concern • Not on file Social History Narrative • No narrative on file BP 137 / 90 | Pulse 112 | Temp ( Src ) 38.8 °C ( 101.8 °F ) ( Oral ) | Resp 19 | LMP 07 / 23 / 2013 Gen : NAD Abd : soft , NT , ND , no fundal tenderness No CVA tenderness Incision : clean , no purulent drainage , small area of erythema surrounding the middle of the incision There is a small defect in the incision line - 4 cm at the midpoint of the incision and less than 1 cm on the distal right aspect of the incision line ; however the underlying tissue is healing well , pink , and healthy .

2020-10-16 17:16:02 - Transformer_NER - WARNING - 
Sentence after tokenization is too long (expect less than 126 but got 830).
You have to inc

Past Medical History Diagnosis Date • Hypertension • Discoid lupus • Sjogren ' s disease • COPD ( chronic obstructive pulmonary disease ) • Allergy to environmental factors • Colitis • Colon polyp • Chronic kidney disease • UTI ( urinary tract infection ) • Diverticulitis • Diverticulosis • GERD ( gastroesophageal reflux disease ) • Pancreatitis • Right thyroid nodule 6 / 1 / 2015 • Carotid stenosis 6 / 1 / 2015 Past Surgical History Procedure Laterality Date • Bladder surgery 2011 • Kidney surgery 2010 stent placed • Colonoscopy w / or w / o biopsy N / A 7 / 18 / 2014 COLONOSCOPY W / OR W / O BIOPSY performed by Munoz , Juan , MD at JAX GI OR • Colonoscopy • Polypectomy Family History Problem Relation Age of Onset • Cancer Mother • Diabetes Father • Diabetes Sister • Cancer Brother • Diabetes Brother • No Known Problems Maternal Aunt • No Known Problems Maternal Uncle • No Known Problems Paternal Aunt • No Known Problems Paternal Uncle • No Known Problems Maternal Grandmother • No Kno

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [57]:
! ls -l ./SDOH_bert

total 1712000
-rw-rw-r--. 1 zehao.yu zehao.yu        17 Oct 16 21:40 added_tokens.json
-rw-rw-r--. 1 zehao.yu zehao.yu       101 Oct 16 18:09 base_model_name.txt
-rw-rw-r--. 1 zehao.yu zehao.yu 438267529 Oct 16 20:07 checkpoint_10999.bin
-rw-rw-r--. 1 zehao.yu zehao.yu 438267529 Oct 16 20:20 checkpoint_11999.bin
-rw-rw-r--. 1 zehao.yu zehao.yu 438267529 Oct 16 20:48 checkpoint_13999.bin
-rw-rw-r--. 1 zehao.yu zehao.yu      5894 Oct 16 21:40 config.json
-rw-rw-r--. 1 zehao.yu zehao.yu      1711 Oct 16 18:09 label2idx.json
-rw-rw-r--. 1 zehao.yu zehao.yu 438018551 Oct 16 20:48 pytorch_model.bin
-rw-rw-r--. 1 zehao.yu zehao.yu       112 Oct 16 21:40 special_tokens_map.json
-rw-rw-r--. 1 zehao.yu zehao.yu        48 Oct 16 21:40 tokenizer_config.json
-rw-rw-r--. 1 zehao.yu zehao.yu    231508 Oct 16 21:40 vocab.txt


In [58]:
file_ids = set()
enss = []

for fn in Path(test_root).glob("*.ann"):
    file_ids.add(fn.stem)
    _, ens, _ = read_annotation_brat(fn)
    #print( _)
    enss.extend(ens)
print("training files: ", len(file_ids), list(file_ids)[:5])
print("total training eneitites: ", len(enss))
print("Entities distribution by types:\n", "\n".join([str(c) for c in Counter([each[1] for each in enss]).most_common()]))

training files:  130 ['IRB201901754_NOTE_933765_0', 'IRB201901754_NOTE_616849_0', 'IRB201901754_NOTE_535204_0', 'note_105249_0', 'note_118303_0']
total training eneitites:  1124
Entities distribution by types:
 ('SMOKING', 244)
('GENEDER', 204)
('ALCOHOL', 124)
('DRUG_ABUSE', 117)
('LIVING_SUPPLY', 113)
('MARITAL_STATUS', 102)
('SEXUAL_ACTIVITY', 64)
('RACE', 24)
('LIVING_CONDITION', 20)
('EDUCATION_GENERAL', 17)
('ETHNICITY', 14)
('EMPLOYMENT_STATUS', 12)
('ALCOHOL_ABUSE', 10)
('PHYSICAL_ACTIVITY', 9)
('OCCUPATION', 9)
('PERSONAL_SAFETY', 8)
('ABUSE', 6)
('LANGUAGE', 5)
('SOCIAL_COHENSION', 5)
('TRANSPOTATION', 4)
('IPV', 4)
('WORKING_CONDITION', 3)
('LITERACY', 2)
('FINACIAL_CONSTRAIN', 2)
('EDUCATION_CHILDHOOD', 1)
('EDUCATION_HIGHLEVEL', 1)


In [59]:
# generate bio
test_root = Path(test_root)
test_bio = "./bio/round_3"
output_root = Path(test_bio)
output_root.mkdir(parents=True, exist_ok=True)

for fn in test_root.glob("*.txt"):
    txt_fn = fn
    bio_fn = output_root / (fn.stem + ".bio.txt")
    
    txt, sents = pre_processing(txt_fn, deid_pattern=MIMICIII_PATTERN)
    nsents, sent_bound = generate_BIO(sents, [], file_id=fid, no_overlap=False)
    
    BIOdata_to_file(bio_fn, nsents)

2020-10-17 10:57:05,155 INFO sentence boundary detection class initiated.
2020-10-17 10:57:05,156 INFO word level tokenization with replace_number set to False
2020-10-17 10:57:05,157 INFO current processing new_round_3/IRB201901754_NOTE_895442_0.txt ...
2020-10-17 10:57:05,186 INFO process note_97466_2 file
2020-10-17 10:57:05,236 INFO sentence boundary detection class initiated.
2020-10-17 10:57:05,237 INFO word level tokenization with replace_number set to False
2020-10-17 10:57:05,237 INFO current processing new_round_3/note_105249_0.txt ...
2020-10-17 10:57:05,263 INFO process note_97466_2 file
2020-10-17 10:57:05,315 INFO sentence boundary detection class initiated.
2020-10-17 10:57:05,315 INFO word level tokenization with replace_number set to False
2020-10-17 10:57:05,316 INFO current processing new_round_3/IRB201901754_NOTE_1163791_0.txt ...
2020-10-17 10:57:05,357 INFO process note_97466_2 file
2020-10-17 10:57:05,413 INFO sentence boundary detection class initiated.
2020-10-

2020-10-17 10:57:07,369 INFO process note_97466_2 file
2020-10-17 10:57:07,419 INFO sentence boundary detection class initiated.
2020-10-17 10:57:07,420 INFO word level tokenization with replace_number set to False
2020-10-17 10:57:07,421 INFO current processing new_round_3/IRB201901754_NOTE_504433_0.txt ...
2020-10-17 10:57:07,462 INFO process note_97466_2 file
2020-10-17 10:57:07,512 INFO sentence boundary detection class initiated.
2020-10-17 10:57:07,513 INFO word level tokenization with replace_number set to False
2020-10-17 10:57:07,514 INFO current processing new_round_3/note_221386_0.txt ...
2020-10-17 10:57:07,519 WARNING '1.73M2' cannot be parsed by current rule.
2020-10-17 10:57:07,539 INFO process note_97466_2 file
2020-10-17 10:57:07,590 INFO sentence boundary detection class initiated.
2020-10-17 10:57:07,591 INFO word level tokenization with replace_number set to False
2020-10-17 10:57:07,592 INFO current processing new_round_3/IRB201901754_NOTE_1166357_1.txt ...
2020-10

2020-10-17 10:57:09,566 INFO current processing new_round_3/IRB201901754_NOTE_527044_0.txt ...
2020-10-17 10:57:09,590 INFO process note_97466_2 file
2020-10-17 10:57:09,641 INFO sentence boundary detection class initiated.
2020-10-17 10:57:09,642 INFO word level tokenization with replace_number set to False
2020-10-17 10:57:09,642 INFO current processing new_round_3/note_186501_0.txt ...
2020-10-17 10:57:09,661 INFO process note_97466_2 file
2020-10-17 10:57:09,710 INFO sentence boundary detection class initiated.
2020-10-17 10:57:09,711 INFO word level tokenization with replace_number set to False
2020-10-17 10:57:09,712 INFO current processing new_round_3/note_180969_3.txt ...
2020-10-17 10:57:09,732 INFO process note_97466_2 file
2020-10-17 10:57:09,781 INFO sentence boundary detection class initiated.
2020-10-17 10:57:09,782 INFO word level tokenization with replace_number set to False
2020-10-17 10:57:09,783 INFO current processing new_round_3/IRB201901754_NOTE_915175_1.txt ...
2

2020-10-17 10:57:11,844 INFO sentence boundary detection class initiated.
2020-10-17 10:57:11,845 INFO word level tokenization with replace_number set to False
2020-10-17 10:57:11,845 INFO current processing new_round_3/IRB201901754_NOTE_326591_0.txt ...
2020-10-17 10:57:11,865 INFO process note_97466_2 file
2020-10-17 10:57:11,915 INFO sentence boundary detection class initiated.
2020-10-17 10:57:11,916 INFO word level tokenization with replace_number set to False
2020-10-17 10:57:11,916 INFO current processing new_round_3/note_222435_10.txt ...
2020-10-17 10:57:11,939 INFO process note_97466_2 file
2020-10-17 10:57:11,990 INFO sentence boundary detection class initiated.
2020-10-17 10:57:11,991 INFO word level tokenization with replace_number set to False
2020-10-17 10:57:11,992 INFO current processing new_round_3/note_94882_1.txt ...
2020-10-17 10:57:12,062 INFO process note_97466_2 file
2020-10-17 10:57:12,129 INFO sentence boundary detection class initiated.
2020-10-17 10:57:12,13

2020-10-17 10:57:14,184 INFO current processing new_round_3/note_168941_6.txt ...
2020-10-17 10:57:14,203 INFO process note_97466_2 file
2020-10-17 10:57:14,251 INFO sentence boundary detection class initiated.
2020-10-17 10:57:14,252 INFO word level tokenization with replace_number set to False
2020-10-17 10:57:14,252 INFO current processing new_round_3/note_284840_0.txt ...
2020-10-17 10:57:14,271 INFO process note_97466_2 file
2020-10-17 10:57:14,319 INFO sentence boundary detection class initiated.
2020-10-17 10:57:14,320 INFO word level tokenization with replace_number set to False
2020-10-17 10:57:14,321 INFO current processing new_round_3/note_179302_2.txt ...
2020-10-17 10:57:14,342 INFO process note_97466_2 file
2020-10-17 10:57:14,391 INFO sentence boundary detection class initiated.
2020-10-17 10:57:14,392 INFO word level tokenization with replace_number set to False
2020-10-17 10:57:14,392 INFO current processing new_round_3/IRB201901754_NOTE_1133139_0.txt ...
2020-10-17 10

In [60]:

! export CUDA_VISIBLE_DEVICES=1

# use format 1 for BRAT, 2 for BioC, 0 as default for BIO
! MKL_THREADING_LAYER=GNU python ./ClinicalTransformerNER/src/run_transformer_batch_prediction.py \
      --model_type bert \
      --pretrained_model ./SDOH_bert \
      --raw_text_dir ./new_round_3 \
      --preprocessed_text_dir ./bio/round_3 \
      --output_dir ./round_3_output \
      --max_seq_length 128 \
      --do_lower_case \
      --eval_batch_size 8 \
      --log_file ./log.txt\
      --do_format 1 \
      --do_copy \
      --data_has_offset_information

In [64]:
#round4

In [65]:
# generate bio
test_root = Path('./new_round_4')
test_bio = "./bio/round_4"
output_root = Path(test_bio)
output_root.mkdir(parents=True, exist_ok=True)

for fn in test_root.glob("*.txt"):
    txt_fn = fn
    bio_fn = output_root / (fn.stem + ".bio.txt")
    
    txt, sents = pre_processing(txt_fn, deid_pattern=MIMICIII_PATTERN)
    nsents, sent_bound = generate_BIO(sents, [], file_id=fid, no_overlap=False)
    
    BIOdata_to_file(bio_fn, nsents)

2020-11-05 13:12:57,306 INFO sentence boundary detection class initiated.
2020-11-05 13:12:57,307 INFO word level tokenization with replace_number set to False
2020-11-05 13:12:57,308 INFO current processing new_round_4/IRB201901754_NOTE_696348_1.txt ...
2020-11-05 13:12:57,337 INFO process note_97466_2 file
2020-11-05 13:12:57,387 INFO sentence boundary detection class initiated.
2020-11-05 13:12:57,388 INFO word level tokenization with replace_number set to False
2020-11-05 13:12:57,389 INFO current processing new_round_4/note_78772_2.txt ...
2020-11-05 13:12:57,407 INFO process note_97466_2 file
2020-11-05 13:12:57,453 INFO sentence boundary detection class initiated.
2020-11-05 13:12:57,454 INFO word level tokenization with replace_number set to False
2020-11-05 13:12:57,455 INFO current processing new_round_4/IRB201901754_NOTE_634714_0.txt ...
2020-11-05 13:12:57,476 INFO process note_97466_2 file
2020-11-05 13:12:57,524 INFO sentence boundary detection class initiated.
2020-11-05

2020-11-05 13:12:59,510 INFO process note_97466_2 file
2020-11-05 13:12:59,574 INFO sentence boundary detection class initiated.
2020-11-05 13:12:59,575 INFO word level tokenization with replace_number set to False
2020-11-05 13:12:59,576 INFO current processing new_round_4/IRB201901754_NOTE_3401_0.txt ...
2020-11-05 13:12:59,593 INFO process note_97466_2 file
2020-11-05 13:12:59,641 INFO sentence boundary detection class initiated.
2020-11-05 13:12:59,642 INFO word level tokenization with replace_number set to False
2020-11-05 13:12:59,642 INFO current processing new_round_4/IRB201901754_NOTE_985159_0.txt ...
2020-11-05 13:12:59,666 INFO process note_97466_2 file
2020-11-05 13:12:59,715 INFO sentence boundary detection class initiated.
2020-11-05 13:12:59,716 INFO word level tokenization with replace_number set to False
2020-11-05 13:12:59,716 INFO current processing new_round_4/note_139800_1.txt ...
2020-11-05 13:12:59,762 INFO process note_97466_2 file
2020-11-05 13:12:59,819 INFO s

2020-11-05 13:13:01,605 INFO process note_97466_2 file
2020-11-05 13:13:01,655 INFO sentence boundary detection class initiated.
2020-11-05 13:13:01,656 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:01,656 INFO current processing new_round_4/note_188677_2.txt ...
2020-11-05 13:13:01,675 INFO process note_97466_2 file
2020-11-05 13:13:01,723 INFO sentence boundary detection class initiated.
2020-11-05 13:13:01,724 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:01,725 INFO current processing new_round_4/note_196683_1.txt ...
2020-11-05 13:13:01,745 INFO process note_97466_2 file
2020-11-05 13:13:01,792 INFO sentence boundary detection class initiated.
2020-11-05 13:13:01,793 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:01,794 INFO current processing new_round_4/IRB201901754_NOTE_520138_0.txt ...
2020-11-05 13:13:01,822 INFO process note_97466_2 file
2020-11-05 13:13:01,871 INFO sentence bou

2020-11-05 13:13:03,604 INFO process note_97466_2 file
2020-11-05 13:13:03,652 INFO sentence boundary detection class initiated.
2020-11-05 13:13:03,653 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:03,653 INFO current processing new_round_4/IRB201901754_NOTE_1237682_1.txt ...
2020-11-05 13:13:03,676 INFO process note_97466_2 file
2020-11-05 13:13:03,725 INFO sentence boundary detection class initiated.
2020-11-05 13:13:03,726 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:03,726 INFO current processing new_round_4/note_189382_1.txt ...
2020-11-05 13:13:03,760 INFO process note_97466_2 file
2020-11-05 13:13:03,812 INFO sentence boundary detection class initiated.
2020-11-05 13:13:03,813 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:03,814 INFO current processing new_round_4/note_90693_0.txt ...
2020-11-05 13:13:03,824 WARNING '1.73M2' cannot be parsed by current rule.
2020-11-05 13:13:03,8

2020-11-05 13:13:05,754 INFO current processing new_round_4/IRB201901754_NOTE_599212_0.txt ...
2020-11-05 13:13:05,775 INFO process note_97466_2 file
2020-11-05 13:13:05,824 INFO sentence boundary detection class initiated.
2020-11-05 13:13:05,825 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:05,825 INFO current processing new_round_4/IRB201901754_NOTE_832658_0.txt ...
2020-11-05 13:13:05,863 INFO process note_97466_2 file
2020-11-05 13:13:05,915 INFO sentence boundary detection class initiated.
2020-11-05 13:13:05,916 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:05,917 INFO current processing new_round_4/IRB201901754_NOTE_95628_0.txt ...
2020-11-05 13:13:05,939 INFO process note_97466_2 file
2020-11-05 13:13:05,988 INFO sentence boundary detection class initiated.
2020-11-05 13:13:05,989 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:05,989 INFO current processing new_round_4/note_128823

...

2020-11-05 13:13:21,199 INFO process note_97466_2 file
2020-11-05 13:13:21,249 INFO sentence boundary detection class initiated.
2020-11-05 13:13:21,250 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:21,251 INFO current processing new_round_4/IRB201901754_NOTE_700203_0.txt ...
2020-11-05 13:13:21,284 INFO process note_97466_2 file
2020-11-05 13:13:21,335 INFO sentence boundary detection class initiated.
2020-11-05 13:13:21,336 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:21,337 INFO current processing new_round_4/note_89021_1.txt ...
2020-11-05 13:13:21,379 INFO process note_97466_2 file
2020-11-05 13:13:21,432 INFO sentence boundary detection class initiated.
2020-11-05 13:13:21,433 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:21,434 INFO current processing new_round_4/note_106875_1.txt ...
2020-11-05 13:13:21,452 INFO process note_97466_2 file
2020-11-05 13:13:21,499 INFO sentence boun

2020-11-05 13:13:23,452 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:23,453 INFO current processing new_round_4/IRB201901754_NOTE_661687_0.txt ...
2020-11-05 13:13:23,482 INFO process note_97466_2 file
2020-11-05 13:13:23,532 INFO sentence boundary detection class initiated.
2020-11-05 13:13:23,533 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:23,533 INFO current processing new_round_4/IRB201901754_NOTE_513814_0.txt ...
2020-11-05 13:13:23,553 INFO process note_97466_2 file
2020-11-05 13:13:23,602 INFO sentence boundary detection class initiated.
2020-11-05 13:13:23,603 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:23,603 INFO current processing new_round_4/note_263606_1.txt ...
2020-11-05 13:13:23,610 WARNING '1.73M2' cannot be parsed by current rule.
2020-11-05 13:13:23,637 INFO process note_97466_2 file
2020-11-05 13:13:23,690 INFO sentence boundary detection class initiated.
2020-11-

2020-11-05 13:13:25,524 INFO process note_97466_2 file
2020-11-05 13:13:25,578 INFO sentence boundary detection class initiated.
2020-11-05 13:13:25,579 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:25,579 INFO current processing new_round_4/IRB201901754_NOTE_930365_0.txt ...
2020-11-05 13:13:25,603 INFO process note_97466_2 file
2020-11-05 13:13:25,655 INFO sentence boundary detection class initiated.
2020-11-05 13:13:25,656 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:25,657 INFO current processing new_round_4/note_293938_1.txt ...
2020-11-05 13:13:25,665 WARNING '1.73M2' cannot be parsed by current rule.
2020-11-05 13:13:25,691 INFO process note_97466_2 file
2020-11-05 13:13:25,743 INFO sentence boundary detection class initiated.
2020-11-05 13:13:25,744 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:25,745 INFO current processing new_round_4/note_35842_1.txt ...
2020-11-05 13:13:25,75

2020-11-05 13:13:27,619 INFO process note_97466_2 file
2020-11-05 13:13:27,670 INFO sentence boundary detection class initiated.
2020-11-05 13:13:27,671 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:27,671 INFO current processing new_round_4/note_306486_0.txt ...
2020-11-05 13:13:27,704 INFO process note_97466_2 file
2020-11-05 13:13:27,755 INFO sentence boundary detection class initiated.
2020-11-05 13:13:27,755 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:27,756 INFO current processing new_round_4/IRB201901754_NOTE_946204_0.txt ...
2020-11-05 13:13:27,773 INFO process note_97466_2 file
2020-11-05 13:13:27,820 INFO sentence boundary detection class initiated.
2020-11-05 13:13:27,821 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:27,822 INFO current processing new_round_4/IRB201901754_NOTE_313883_0.txt ...
2020-11-05 13:13:27,850 INFO process note_97466_2 file
2020-11-05 13:13:27,902 INFO

2020-11-05 13:13:29,905 INFO process note_97466_2 file
2020-11-05 13:13:29,957 INFO sentence boundary detection class initiated.
2020-11-05 13:13:29,958 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:29,959 INFO current processing new_round_4/note_198897_1.txt ...
2020-11-05 13:13:29,977 INFO process note_97466_2 file
2020-11-05 13:13:30,025 INFO sentence boundary detection class initiated.
2020-11-05 13:13:30,026 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:30,027 INFO current processing new_round_4/note_306148_1.txt ...
2020-11-05 13:13:30,047 INFO process note_97466_2 file
2020-11-05 13:13:30,096 INFO sentence boundary detection class initiated.
2020-11-05 13:13:30,096 INFO word level tokenization with replace_number set to False
2020-11-05 13:13:30,097 INFO current processing new_round_4/note_288238_1.txt ...
2020-11-05 13:13:30,107 WARNING '1.73M2' cannot be parsed by current rule.
2020-11-05 13:13:30,135 INFO proce

In [66]:
! export CUDA_VISIBLE_DEVICES=1

# use format 1 for BRAT, 2 for BioC, 0 as default for BIO
! MKL_THREADING_LAYER=GNU python ./ClinicalTransformerNER/src/run_transformer_batch_prediction.py \
      --model_type bert \
      --pretrained_model ./SDOH_bert \
      --raw_text_dir ./new_round_4 \
      --preprocessed_text_dir ./bio/round_4 \
      --output_dir ./round_4_output \
      --max_seq_length 128 \
      --do_lower_case \
      --eval_batch_size 8 \
      --log_file ./log.txt\
      --do_format 1 \
      --do_copy \
      --data_has_offset_information